# Assignment 1: Planning using Heuristic Search

**Felipe Meneguzzi**  
**Mauricio Magnaguagno (PhD Student)**  
**Leonardo Rosa Amado (PhD Student)**
**Gabriel Paludo Licks (MSc Student)**

Introduction to Artificial Intelligence (4646A-4) and Applied Artificial Intelligence (4621A-4):
- Assigned: 06 April
- Due: 05 May

## Assignment Overview

<img align="right" src="planning-assignment.png"/>

The goal of this work is to implement the core functions of an automated planner and benchmark a number of heuristics. You will implement three main functions in this assignment:
- Implement the **Max-Cost** ($h^{max}$) heuristic function.
- Implement a function capable of validating a plan given a domain and a problem.
- Finally, implement the heuristic search **A\***

After implementing the required functions, you must write a 2-page paper. The entire package must be delivered using GitHub, where your implemented functions must be contained in this Jupyter Notebook, and the paper as a separate **pdf** file committed in the same Github repository (the template is in the ```paper``` folder).

## Experimentation

- You can test your implementation with the provided domains and problems:
  - [blocksworld](examples/blocksworld)
  - [dinner](examples/dinner)
  - [dwr](examples/dwr)
  - [tsp](examples/tsp)

- Planning tools and extra domains and problems to sanity check your own implementation:
  - [Web-Planner](https://web-planner.herokuapp.com/)
  - [editor.planning.domains](http://editor.planning.domains/)
  - IPC domains and problems can be found in [potassco/pddl-instances](https://github.com/potassco/pddl-instances)


## Grading

In order to properly evaluate your work and thought process, you will write a **2-page** report in the AAAI two-column format explaining your encoding and experiments. 
These guidelines are to be followed **exactly**. 
**Reports that are less than two pages of actual content, or not in format will receive 0 marks for the report criterion.** 
This report will be included in the deliverables of the assignment. 
[The formatting instructions are available at ShareLatex (AAAI Press)](https://www.sharelatex.com/templates/journals/aaai-press). 
The report must have the following sections:

- An introduction with your understanding of the problem domain, outlining the remainder of the paper;
- Three sections explaining each part of your implementation (search, heuristic, and validator).
- One experimentation section where you measure the performance of the planner using your action formalisation for each of the domains, on multiple problems.
- One conclusion section, where you will summarise your experience in encoding planning domains and discuss the performance of the planner, and any limitations encountered in solving the problems you encoded.

Grading will consider elements of your encoding, experimentation and reporting of the work done. 
The criteria, as well as their weight in the final grade is as follows:

- Implementation (70%):
  - Heuristic function (20%);
  - Validator (20%);
  - Heuristic search (30%):
      - Correctness and optimality (20%); and
      - Runtime efficiency (10%).
- Overall report readability (20%) — how accessible and coherent your explanation of your implementation is;
- Code readability (10%).

## Important Information

**Corrections:** From time to time, students or staff find errors (e.g., typos, unclear instructions, etc.) in the assignment specification. In that case, a corrected version of this file will be produced, announced, and distributed for you to commit and push into your repository. Because of that, you are NOT to modify the README.md file in any way to avoid conflicts.

**Late submissions & extensions:** You have a 24 hour grace period with a penalty of 10% of the maximum mark, which increases to 50% until 48 hours after the due date, and 100% penalty thereafter. Extensions will only be permitted in _exceptional_ circumstances. 

**About this repo:** You must ALWAYS keep your fork private and never share it with anybody in or outside the course, even after the course is completed. You are not allowed to make another repository copy outside the provided GitHub Classroom without the written permission of the teaching staff.

> **_Please do not distribute or post solutions to any of the projects and notebooks._**

**Collaboration Policy:** You must work on this project **individually**. 
You are free to discuss high-level design issues with the people in your class, but every aspect of your actual formalisation must be entirely your own work.
Furthermore, there can be no textual similarities in the reports generated by each group. 
Plagiarism, no matter the degree, will result in forfeiture of the entire grade of this assignment.

**We are here to help!:** We are here to help you! But we don't know you need help unless you tell us. We expect reasonable effort from you side, but if you get stuck or have doubts, please seek help by creating an issue in the repository and assigning it to the instructor. Always keep the most updated version of your code pushed to Git so when you create an issue, the teaching staff can look into your code to help. 

**Silence Policy:** A silence policy will take effect **48 hours** before this assignment is due. This means that no question about this assignment will be answered, whether it is asked on Moodle, by email, or in person. Use the last 48 hours to wrap up and finish your project quietly as well as possible if you have not done so already. Remember it is not mandatory to do all perfect, try to cover as much as possible. By having some silence we reduce anxiety, last minute mistakes, and unreasonable expectations on others. 

## Sections

- [Heuristic](#Heuristic)
  - [Implement the heuristic function](#Implement-the-heuristic-function)
  - [Test heuristic function](#Test-heuristic-function)
- [Validator](#Validator)
  - [Implement the validate function](#Implement-the-validate-function)
  - [Test validate function](#Test-validate-function)
- [Planner](#Planner)
  - [Implement the planner solve function](#Implement-the-planner-solve-function)
  - [Test planner completeness and optimality](#Test-planner-completeness-and-optimality)
  - [Test planner output time](#Test-planner-output-time)

# Auxiliary code
In this cell we provide two methods to aid you in your implementation. First, we provide a method to verify if an action is applicable, in a given a state (all positive preconditions are contained in the state, and no negative preconditions are contained in the state). Second, we provide a method to apply an action in a given state, returning the new resulting state.



In [1]:
def applicable(state, precondition):
    positive, negative = precondition 
    return positive.issubset(state) and not negative.intersection(state)

def apply(state, effects):
    positive, negative = effects
    return frozenset(state.difference(negative).union(positive))

In the next cell, we detail some of the usage of the given base code. 

In [2]:
from pddl.action import Action

# Objects example

# An action to move robot r1 from location l1 to location l2
a1 = Action(
    'move', #Action name
    ['r1', 'l1', 'l2'], #Parameters
    frozenset({('at', 'r1', 'l1'), ('adjacent', 'l1', 'l2')}), #Positive preconditions
    frozenset({('occupied', 'l2')}), #Negative preconditions
    frozenset({('at', 'r1', 'l2'), ('occupied', 'l2')}), #Add effects
    frozenset({('at', 'r1', 'l1'), ('occupied', 'l1')})  #Del effects
)

# Get each element from the action
print(a1.name)
print(a1.parameters)
print(a1.positive_preconditions)
print(a1.negative_preconditions)
print(a1.add_effects)
print(a1.del_effects)

print('---------------------------------------------')

# The list of actions contains all possible actions
actions = [
        a1,
        # ...
    ]

# Only positive literals are present in the initial state
initial_state = frozenset({
    ('on', 'ca', 'pallet'),
    ('at', 'r1', 'l1'),
    ('belong', 'k1', 'l1'),
    ('adjacent', 'l1', 'l2'), ('adjacent', 'l2', 'l1'), ('attached', 'q2', 'l2'),
    ('empty', 'k2'),
    ('attached', 'p1', 'l1'), ('occupied', 'l1'),
    ('empty', 'k1'),
    # ...
})
    
# Goal literals are split in two, positive and negative
positive_goal = frozenset({('in', 'cb', 'p1'), ('in', 'ca', 'p1')})
negative_goal = frozenset()

#Test if the action move (variable a1) is applicable in our initial state (initial_state)
applicable_action = applicable(initial_state, (a1.positive_preconditions, a1.negative_preconditions))
print('Is the action move applicable?', applicable_action)

print('---------------------------------------------')

#Apply the action move in the initial state
resulting_state = apply(initial_state, (a1.add_effects, a1.del_effects))
print('Resulting state:')
for predicate in resulting_state:
    print(predicate)

print('---------------------------------------------')

#Test if the goal was achieved  
goal_achieved = applicable(resulting_state, (positive_goal, negative_goal))
print('Was the goal achieved?', goal_achieved)

print('---------------------------------------------')

# The output plan from the planner is either a list of actions or failure (None)
# An empty plan is valid
plan = []
# Preconditions and effects are empty when obtained from a plan file, may be filled when obtained from the planner
plan = [
    Action('take', ['k1', 'cc', 'cb', 'p1', 'l1'], [], [], [], []), 
    Action('load', ['k1', 'r1', 'cc', 'l1'], [], [], [], []),
    Action('move', ['r1', 'l1', 'l2'], [], [], [], []),
    Action('unload', ['k2', 'r1', 'cc', 'l2'], [], [], [], [])
    # ...
]
# Failure
plan = None

# A valid plan is either true or false
valid_plan   = True
invalid_plan = False

move
['r1', 'l1', 'l2']
frozenset({('at', 'r1', 'l1'), ('adjacent', 'l1', 'l2')})
frozenset({('occupied', 'l2')})
frozenset({('occupied', 'l2'), ('at', 'r1', 'l2')})
frozenset({('at', 'r1', 'l1'), ('occupied', 'l1')})
---------------------------------------------
Is the action move applicable? True
---------------------------------------------
Resulting state:
('attached', 'q2', 'l2')
('empty', 'k1')
('on', 'ca', 'pallet')
('at', 'r1', 'l2')
('empty', 'k2')
('adjacent', 'l2', 'l1')
('occupied', 'l2')
('adjacent', 'l1', 'l2')
('attached', 'p1', 'l1')
('belong', 'k1', 'l1')
---------------------------------------------
Was the goal achieved? False
---------------------------------------------


# Heuristics

## Implement heuristic functions


### Max-cost
You will implement the Max-cost heuristic. 
Return estimated distance between current ``state`` $s$ and ``goal`` $g$, a number between 0 (when $s \models g$) and infinity (when $g$ is unreachable).

$$
h^{max}(s,g)=\max_{g_i \in g}
\begin{cases}
0, & \text{if } g_i \in s\\
\min \{cost(a) + h^{max}(s,pre(a))\text{ | }a \in A \text{ and }g_i \in \text{eff}(a)\} & \text{otherwise}\\
\end{cases}
$$

where $cost(a)$ is the cost of action $a$ ($1$ if not specified), $pre(a)$ is the set of precoditions of action $a$, and $eff(a)$ is the set of effects of action $a$. Your code must be contained in the ``h(self, actions, state, goals)`` function in the cell below. You can create additional functions (do not forget to comment the code intelligibly). H takes the following inputs:
- ``actions``: list of ground actions
- ``state``: current state
- ``goals``: tuple with (positive predicates, negative predicates) of the goal

## Relaxed Planning Graph
In this section, we provide a python implementation of how to build the Relaxed Planning Graph. You can use this implementation to obtain the max-cost heuristic, instead of the previous formula (with only a few modifications). Use wisely!

```python
def build_rpg(actions, state, goals):
    i = 0
    factlevel = [state]
    actionlevel = []
    positive_goals = goals[0]
    while not positive_goals.issubset(factlevel[i]):
        # actionlevel[i]
        actionlevel.append([a for a in actions if a.positive_preconditions.issubset(factlevel[i])])
        # factlevel[i+1]
        factlevel.append(factlevel[i].union([pre for a in actionlevel[i] for pre in a.add_effects]))
        if factlevel[i+1] == factlevel[i]:
            return "G unreachable"
        i += 1
    return (factlevel, actionlevel)
```

In [3]:
from pddl.heuristic import Heuristic

class MaxHeuristic(Heuristic):
    # Positive goals and negative goals in a tuple
    def h(self, actions, state, goals):
        i = 0
        factlevel = [state]
        actionlevel = []
        positive_goals = goals[0]
        while not positive_goals.issubset(factlevel[i]):
            # actionlevel[i]
            actionlevel.append(
                [a for a in actions
                 if a.positive_preconditions.issubset(factlevel[i])])
            # factlevel[i+1]
            factlevel.append(factlevel[i].union(
                [pre for a in actionlevel[i]
                 for pre in a.add_effects]))
            if factlevel[i+1] == factlevel[i]:
                return float("inf")
            i += 1
        return i

## Test the heuristic function

We will test the Max Heuristic using 3 different domains, dinner, tsp and dwr. The state used is the initial state of each problem. 

At each execution we show the expected value for the Max-cost heuristic.

In [4]:
from pddl.pddl_parser import PDDLParser
from pddl.action import Action

# The following should be visible to the students
# Load some domain and some problem
dwr = "examples/dwr/dwr.pddl"
pb1_dwr = "examples/dwr/pb1.pddl"
pb2_dwr = "examples/dwr/pb2.pddl"

tsp = "examples/tsp/tsp.pddl"
pb1_tsp = "examples/tsp/pb1.pddl"

dinner = "examples/dinner/dinner.pddl"
pb1_dinner = "examples/dinner/pb1.pddl"

def parse_domain_problem(domain, problem):
    parser = PDDLParser()
    parser.parse_domain(domain)
    parser.parse_problem(problem)
    # Grounding process
    actions = []
    for action in parser.actions:
        for act in action.groundify(parser.objects):
            actions.append(act)
    return parser, actions

def test_heuristic(domain, problem, h, expected):
    parser, actions = parse_domain_problem(domain, problem)
    v = h.h(actions, parser.state, (parser.positive_goals, parser.negative_goals))
    print("Expected " + str(expected) + ", got:", str(v) + ('. Correct!' if v == expected else '. False!'))

# Apply Hmax to initial states of many problems from many domains
h = MaxHeuristic()
test_heuristic(dwr, pb1_dwr, h, 6)
test_heuristic(dwr, pb2_dwr, h, 0)
test_heuristic(tsp, pb1_tsp, h, 2)
test_heuristic(dinner, pb1_dinner, h, 1)


Expected 6, got: 6. Correct!
Expected 0, got: 0. Correct!
Expected 2, got: 2. Correct!
Expected 1, got: 1. Correct!


# Validator

## Implement the validate function
You will now implement a validator capable of verifying if a plan is valid to a specific domain and problem. The validator must return **True** if and only if the given plan is applicable and reaches the specified goal, and **False** if the plan itself is **not** applicable **or**  the given plan does **not** achieve the specified goal. Your code must be contained in the ```validate(self, actions, initial_state, goals, plan)``` function in the cell below. You can create additional functions (do not forget to comment the code intelligibly). Validate takes the following inputs:
- ``actions``: list of ground actions
- ``initial_state``: initial state of the problem file
- ``goals``: tuple with (positive predicates, negative predicates) of the goal
- ``plan``: plan parsed from a plan trace

In [5]:
from pddl.pddl_parser import PDDLParser
from pddl.action import Action

class Validator:

    def parse_plan(self, filename):
        with open(filename,'r') as f:
            plan = []
            for act in f.read().splitlines():
                act = act[1:-1].split()
                plan.append(Action(act[0], tuple(act[1:]), [], [], [], []))
            return plan

    def validate_file(self, domainfile, problemfile, planfile):
        return self.validate_plan(domainfile, problemfile, self.parse_plan(planfile))

    def validate_plan(self, domainfile, problemfile, plan):
        # Parser
        parser = PDDLParser()
        parser.parse_domain(domainfile)
        parser.parse_problem(problemfile)
        # Grounding process
        ground_actions = []
        for action in parser.actions:
            for act in action.groundify(parser.objects):
                ground_actions.append(act)
        return self.validate(ground_actions, parser.state, (parser.positive_goals, parser.negative_goals), plan)
    
    # =====================================
    # Params:
    # actions -> list of ground actions
    # initial_state -> initial state of the problem file
    # goals -> tuple with (positive predicates, negative predicates) of the goal
    # plan -> plan parsed from a plan trace
    # =====================================

    #Positive goals and negative goals in a tuple
    def validate(self, actions, initial_state, goals, plan):
        actual_state = initial_state
        for a in actions:
            for p in plan:
                if p.name == a.name:
                    if p.parameters == a.parameters:
                        p.positive_preconditions = a.positive_preconditions
                        p.negative_preconditions = a.negative_preconditions
                        p.add_effects = a.add_effects
                        p.del_effects = a.del_effects

        for p in plan:
            applicable_action = applicable(
                actual_state, (p.positive_preconditions, p.negative_preconditions))
            if applicable_action == True:
                actual_state = apply(
                    actual_state, (p.add_effects, p.del_effects))

        for g in goals:
            if g.issubset(actual_state):
                return True
            else:
                return False

## Test the validate function
In this test, we verify the correctness of the implemented validator using the **[dwr](examples/dwr)** domain. Consider running more tests to ensure the correctness of the implemented function.

In [6]:
dwr = "examples/dwr/dwr.pddl"
pb1 = "examples/dwr/pb1.pddl"
plan1 = "examples/dwr/dwr_pb1_bfs.plan"
plan2 = "examples/dwr/dwr_pb1_heuristic.plan"
plan_empty = "examples/dwr/empty.plan"
val = Validator()
print("Expected True, got:", str(val.validate_file(dwr, pb1, plan1)))
print("Expected True, got:", str(val.validate_file(dwr, pb1, plan2)))
print("Expected False, got:", str(val.validate_file(dwr, pb1, plan_empty)))


Expected True, got: True
Expected True, got: True
Expected False, got: False


# Planner

## Implement the planner ```solve``` function
You will implement the **A\*** search. This search must use the implemented **Max-cost** heuristic. The search receives a **domain** pddl file and a **problem** pddl file (both are already parsed for you). The search must always return an optimal plan, given that there is a solution for the given problem in the specified domain. Your code must be contained in the ``solve(self, actions, state, goals)`` function (in the following cell). Solve takes the following inputs:
- ``actions``: list of grounded actions
- ``state``: initial state of the problem file
- ``goals``: tuple with (positive predicates, negative predicates) of the goal

In [7]:
from pddl.pddl_planner import PDDLPlanner
import sys
import queue as queue

class HeuristicPlanner(PDDLPlanner):
    

    def __init__(self, heuristic=MaxHeuristic(), verbose=False, collect_stats=False):
        super().__init__(verbose,collect_stats)
        self.h = heuristic

    # -----------------------------------------------
    # Solve
    # -----------------------------------------------
    
    # =====================================
    # Params:
    # actions -> list of grounded actions
    # state -> initial state of the problem file
    # goals -> tuple with (positive predicates, negative predicates) of the goal
    # =====================================
    
    #Positive goals and negative goals in a tuple
    def solve(self, actions, state, goals):
        # YOUR CODE HERE
        #raise NotImplementedError()
        Tree = []
        plan = []
        less = Action('take', ['k1', 'cc', 'cb', 'p1', 'l1'], [], [], [], [])
        closed = []
        i = 0
        frontier = queue.PriorityQueue()
        frontier.put((0, state, 0))

        while not (frontier.empty() == True):
            n = frontier.get()
            plan.append(n[1])
            actual_state = n[1]
            closed.append(actual_state)
            if applicable(actual_state, goals):
                actual_state = frontier[0]
                while not actual_state.issubset(goals):
                    return plan

            for a in actions:
                applicable_action = applicable(
                    actual_state, (a.positive_preconditions, a.negative_preconditions))
                if applicable_action == True:
                    resulting_state = apply(
                        actual_state, (a.add_effects, a.del_effects))
                    if resulting_state not in closed:
                        v = n[2] + h.h(actions, resulting_state, goals)
                        frontier.put((v, resulting_state, n[2]+1))                       

        return plan  # No plan was found

## Test planner completeness and optimality
Here we perform a simple test to verify if the lenght of the plan found by your implementation is step optimal. Please note, that this test does not verify if the plan is valid (but we are going to test this). You can use your own implementation of the validator to verify this (highly recommended).

In [ ]:
#Student_tests
dwr = "examples/dwr/dwr.pddl"
pb1 = "examples/dwr/pb1.pddl"
pb2 = "examples/dwr/pb2.pddl"
planner = HeuristicPlanner()

plan, time = planner.solve_file(dwr, pb1)
print("Expected 17, got:", str(len(plan)) + ('. Correct!' if len(plan) == 17 else '. False!'))
plan, time = planner.solve_file(dwr, pb2)
print("Expected 0, got:", str(len(plan)) + ('. Correct!' if len(plan) == 0 else '. False!'))


6 frozenset({('attached', 'q2', 'l2'), ('top', 'pallet', 'p2'), ('equal', 'cf', 'cf'), ('equal', 'cb', 'cb'), ('on', 'cd', 'pallet'), ('equal', 'cd', 'cd'), ('on', 'cc', 'cb'), ('on', 'ca', 'pallet'), ('top', 'cc', 'p1'), ('top', 'pallet', 'q2'), ('on', 'cf', 'ce'), ('adjacent', 'l2', 'l1'), ('equal', 'cc', 'cc'), ('unloaded', 'r1'), ('adjacent', 'l1', 'l2'), ('equal', 'pallet', 'pallet'), ('belong', 'k1', 'l1'), ('attached', 'p2', 'l2'), ('in', 'ca', 'p1'), ('in', 'cf', 'q1'), ('equal', 'ce', 'ce'), ('attached', 'q1', 'l1'), ('at', 'r1', 'l2'), ('in', 'cb', 'p1'), ('empty', 'k2'), ('in', 'ce', 'q1'), ('occupied', 'l2'), ('attached', 'p1', 'l1'), ('on', 'ce', 'cd'), ('empty', 'k1'), ('equal', 'ca', 'ca'), ('in', 'cc', 'p1'), ('belong', 'k2', 'l2'), ('on', 'cb', 'ca'), ('in', 'cd', 'q1'), ('top', 'cf', 'q1')}) 1 

6 frozenset({('attached', 'q2', 'l2'), ('holding', 'k1', 'cc'), ('top', 'pallet', 'p2'), ('equal', 'cf', 'cf'), ('top', 'cb', 'p1'), ('equal', 'cb', 'cb'), ('on', 'cd', 'palle

8 frozenset({('attached', 'q2', 'l2'), ('top', 'pallet', 'p2'), ('equal', 'cf', 'cf'), ('on', 'cf', 'cc'), ('equal', 'cb', 'cb'), ('on', 'cd', 'pallet'), ('equal', 'cd', 'cd'), ('on', 'cc', 'cb'), ('at', 'r1', 'l1'), ('on', 'ca', 'pallet'), ('top', 'cf', 'p1'), ('top', 'pallet', 'q2'), ('occupied', 'l1'), ('adjacent', 'l2', 'l1'), ('equal', 'cc', 'cc'), ('unloaded', 'r1'), ('adjacent', 'l1', 'l2'), ('equal', 'pallet', 'pallet'), ('belong', 'k1', 'l1'), ('attached', 'p2', 'l2'), ('in', 'ca', 'p1'), ('equal', 'ce', 'ce'), ('attached', 'q1', 'l1'), ('in', 'cb', 'p1'), ('empty', 'k2'), ('in', 'ce', 'q1'), ('attached', 'p1', 'l1'), ('on', 'ce', 'cd'), ('empty', 'k1'), ('in', 'cf', 'p1'), ('equal', 'ca', 'ca'), ('in', 'cc', 'p1'), ('belong', 'k2', 'l2'), ('on', 'cb', 'ca'), ('in', 'cd', 'q1'), ('top', 'ce', 'q1')}) 2 

7 frozenset({('attached', 'q2', 'l2'), ('top', 'cc', 'q1'), ('top', 'pallet', 'p2'), ('equal', 'cf', 'cf'), ('on', 'cc', 'cf'), ('top', 'cb', 'p1'), ('equal', 'cb', 'cb'), ('o

10 frozenset({('attached', 'q2', 'l2'), ('in', 'cd', 'q1'), ('top', 'pallet', 'p2'), ('in', 'ca', 'p1'), ('adjacent', 'l1', 'l2'), ('in', 'cf', 'q1'), ('equal', 'cf', 'cf'), ('equal', 'ce', 'ce'), ('attached', 'q1', 'l1'), ('holding', 'k2', 'cc'), ('equal', 'cb', 'cb'), ('on', 'cd', 'pallet'), ('equal', 'cd', 'cd'), ('in', 'ce', 'q1'), ('attached', 'p1', 'l1'), ('top', 'ca', 'p1'), ('on', 'ce', 'cd'), ('at', 'r1', 'l1'), ('on', 'ca', 'pallet'), ('top', 'pallet', 'q2'), ('equal', 'ca', 'ca'), ('occupied', 'l1'), ('on', 'cf', 'ce'), ('adjacent', 'l2', 'l1'), ('equal', 'cc', 'cc'), ('unloaded', 'r1'), ('attached', 'p2', 'l2'), ('belong', 'k2', 'l2'), ('equal', 'pallet', 'pallet'), ('holding', 'k1', 'cb'), ('belong', 'k1', 'l1'), ('top', 'cf', 'q1')}) 6 

10 frozenset({('attached', 'q2', 'l2'), ('in', 'cd', 'q1'), ('in', 'ca', 'p1'), ('in', 'cf', 'q1'), ('adjacent', 'l1', 'l2'), ('equal', 'cf', 'cf'), ('equal', 'ce', 'ce'), ('attached', 'q1', 'l1'), ('at', 'r1', 'l2'), ('empty', 'k2'), ('e

11 frozenset({('attached', 'q2', 'l2'), ('holding', 'k1', 'cc'), ('top', 'pallet', 'p2'), ('equal', 'cf', 'cf'), ('in', 'cf', 'q2'), ('top', 'cb', 'p1'), ('equal', 'cb', 'cb'), ('on', 'cd', 'pallet'), ('equal', 'cd', 'cd'), ('on', 'ca', 'pallet'), ('adjacent', 'l2', 'l1'), ('equal', 'cc', 'cc'), ('unloaded', 'r1'), ('adjacent', 'l1', 'l2'), ('equal', 'pallet', 'pallet'), ('belong', 'k1', 'l1'), ('attached', 'p2', 'l2'), ('in', 'ca', 'p1'), ('on', 'cf', 'pallet'), ('equal', 'ce', 'ce'), ('attached', 'q1', 'l1'), ('top', 'cf', 'q2'), ('at', 'r1', 'l2'), ('in', 'cb', 'p1'), ('empty', 'k2'), ('in', 'ce', 'q1'), ('occupied', 'l2'), ('attached', 'p1', 'l1'), ('on', 'ce', 'cd'), ('equal', 'ca', 'ca'), ('belong', 'k2', 'l2'), ('on', 'cb', 'ca'), ('in', 'cd', 'q1'), ('top', 'ce', 'q1')}) 6 

12 frozenset({('attached', 'q2', 'l2'), ('top', 'pallet', 'p2'), ('equal', 'cf', 'cf'), ('in', 'cf', 'q2'), ('equal', 'cb', 'cb'), ('on', 'cd', 'pallet'), ('equal', 'cd', 'cd'), ('on', 'cc', 'cb'), ('holdin

11 frozenset({('attached', 'q2', 'l2'), ('in', 'cd', 'q1'), ('top', 'pallet', 'p2'), ('in', 'ca', 'p1'), ('adjacent', 'l1', 'l2'), ('in', 'cf', 'q1'), ('equal', 'cf', 'cf'), ('equal', 'ce', 'ce'), ('attached', 'q1', 'l1'), ('top', 'cc', 'q2'), ('in', 'cc', 'q2'), ('empty', 'k2'), ('equal', 'cb', 'cb'), ('on', 'cd', 'pallet'), ('equal', 'cd', 'cd'), ('in', 'ce', 'q1'), ('attached', 'p1', 'l1'), ('top', 'ca', 'p1'), ('on', 'ce', 'cd'), ('on', 'cc', 'pallet'), ('at', 'r1', 'l1'), ('on', 'ca', 'pallet'), ('equal', 'ca', 'ca'), ('occupied', 'l1'), ('on', 'cf', 'ce'), ('adjacent', 'l2', 'l1'), ('equal', 'cc', 'cc'), ('unloaded', 'r1'), ('attached', 'p2', 'l2'), ('belong', 'k2', 'l2'), ('equal', 'pallet', 'pallet'), ('holding', 'k1', 'cb'), ('belong', 'k1', 'l1'), ('top', 'cf', 'q1')}) 7 

11 frozenset({('attached', 'q2', 'l2'), ('top', 'pallet', 'p1'), ('top', 'pallet', 'p2'), ('equal', 'cf', 'cf'), ('equal', 'cb', 'cb'), ('on', 'cd', 'pallet'), ('equal', 'cd', 'cd'), ('in', 'ca', 'q1'), ('t

...

16 frozenset({('attached', 'q2', 'l2'), ('top', 'pallet', 'p1'), ('equal', 'cf', 'cf'), ('in', 'cc', 'q2'), ('top', 'cb', 'p2'), ('equal', 'cb', 'cb'), ('on', 'cd', 'pallet'), ('equal', 'cd', 'cd'), ('loaded', 'r1', 'ca'), ('at', 'r1', 'l1'), ('occupied', 'l1'), ('on', 'cf', 'ce'), ('adjacent', 'l2', 'l1'), ('equal', 'cc', 'cc'), ('equal', 'pallet', 'pallet'), ('adjacent', 'l1', 'l2'), ('belong', 'k1', 'l1'), ('attached', 'p2', 'l2'), ('on', 'cb', 'pallet'), ('in', 'cf', 'q1'), ('equal', 'ce', 'ce'), ('attached', 'q1', 'l1'), ('top', 'cc', 'q2'), ('empty', 'k2'), ('in', 'cb', 'p2'), ('in', 'ce', 'q1'), ('attached', 'p1', 'l1'), ('on', 'ce', 'cd'), ('on', 'cc', 'pallet'), ('empty', 'k1'), ('equal', 'ca', 'ca'), ('belong', 'k2', 'l2'), ('in', 'cd', 'q1'), ('top', 'cf', 'q1')}) 14 

17 frozenset({('attached', 'q2', 'l2'), ('top', 'pallet', 'p1'), ('equal', 'cf', 'cf'), ('in', 'cc', 'q2'), ('top', 'cb', 'p2'), ('equal', 'cb', 'cb'), ('on', 'cd', 'pallet'), ('equal', 'cd', 'cd'), ('in', 'ca

16 frozenset({('attached', 'q2', 'l2'), ('on', 'cf', 'cb'), ('equal', 'cf', 'cf'), ('equal', 'cb', 'cb'), ('on', 'cd', 'pallet'), ('equal', 'cd', 'cd'), ('on', 'ce', 'cf'), ('at', 'r1', 'l1'), ('top', 'ce', 'p1'), ('on', 'ca', 'pallet'), ('top', 'pallet', 'q2'), ('occupied', 'l1'), ('top', 'cc', 'p2'), ('adjacent', 'l2', 'l1'), ('equal', 'cc', 'cc'), ('unloaded', 'r1'), ('adjacent', 'l1', 'l2'), ('equal', 'pallet', 'pallet'), ('belong', 'k1', 'l1'), ('attached', 'p2', 'l2'), ('in', 'ca', 'p1'), ('top', 'cd', 'q1'), ('equal', 'ce', 'ce'), ('attached', 'q1', 'l1'), ('in', 'cb', 'p1'), ('empty', 'k2'), ('attached', 'p1', 'l1'), ('on', 'cc', 'pallet'), ('empty', 'k1'), ('in', 'cf', 'p1'), ('equal', 'ca', 'ca'), ('in', 'cc', 'p2'), ('in', 'ce', 'p1'), ('belong', 'k2', 'l2'), ('on', 'cb', 'ca'), ('in', 'cd', 'q1')}) 10 

16 frozenset({('attached', 'q2', 'l2'), ('top', 'pallet', 'p1'), ('holding', 'k2', 'cb'), ('equal', 'cf', 'cf'), ('equal', 'cb', 'cb'), ('on', 'cd', 'pallet'), ('equal', 'cd

17 frozenset({('attached', 'q2', 'l2'), ('equal', 'pallet', 'pallet'), ('top', 'pallet', 'p2'), ('in', 'ca', 'p1'), ('top', 'cd', 'q1'), ('equal', 'cf', 'cf'), ('equal', 'ce', 'ce'), ('attached', 'q1', 'l1'), ('top', 'cb', 'p1'), ('in', 'cb', 'p1'), ('equal', 'cb', 'cb'), ('on', 'cd', 'pallet'), ('equal', 'cd', 'cd'), ('attached', 'p1', 'l1'), ('at', 'r1', 'l1'), ('on', 'ca', 'pallet'), ('top', 'pallet', 'q2'), ('occupied', 'l1'), ('loaded', 'r1', 'cc'), ('equal', 'ca', 'ca'), ('holding', 'k2', 'ce'), ('holding', 'k1', 'cf'), ('adjacent', 'l2', 'l1'), ('equal', 'cc', 'cc'), ('belong', 'k2', 'l2'), ('on', 'cb', 'ca'), ('in', 'cd', 'q1'), ('adjacent', 'l1', 'l2'), ('belong', 'k1', 'l1'), ('attached', 'p2', 'l2')}) 12 

16 frozenset({('attached', 'q2', 'l2'), ('on', 'cf', 'cb'), ('top', 'pallet', 'p2'), ('equal', 'cf', 'cf'), ('in', 'cc', 'q2'), ('equal', 'cb', 'cb'), ('on', 'cd', 'pallet'), ('equal', 'cd', 'cd'), ('on', 'ce', 'cf'), ('at', 'r1', 'l1'), ('top', 'ce', 'p1'), ('on', 'ca', '

16 frozenset({('attached', 'q2', 'l2'), ('equal', 'cf', 'cf'), ('on', 'cf', 'cc'), ('on', 'cc', 'ca'), ('top', 'cb', 'p2'), ('equal', 'cb', 'cb'), ('on', 'cd', 'pallet'), ('equal', 'cd', 'cd'), ('on', 'ca', 'pallet'), ('top', 'cf', 'p1'), ('top', 'pallet', 'q2'), ('adjacent', 'l2', 'l1'), ('equal', 'cc', 'cc'), ('unloaded', 'r1'), ('adjacent', 'l1', 'l2'), ('equal', 'pallet', 'pallet'), ('belong', 'k1', 'l1'), ('attached', 'p2', 'l2'), ('on', 'cb', 'pallet'), ('in', 'ca', 'p1'), ('equal', 'ce', 'ce'), ('attached', 'q1', 'l1'), ('at', 'r1', 'l2'), ('empty', 'k2'), ('in', 'cb', 'p2'), ('in', 'ce', 'q1'), ('occupied', 'l2'), ('attached', 'p1', 'l1'), ('on', 'ce', 'cd'), ('empty', 'k1'), ('in', 'cf', 'p1'), ('equal', 'ca', 'ca'), ('in', 'cc', 'p1'), ('belong', 'k2', 'l2'), ('in', 'cd', 'q1'), ('top', 'ce', 'q1')}) 11 

16 frozenset({('attached', 'q2', 'l2'), ('on', 'cf', 'cb'), ('equal', 'cf', 'cf'), ('equal', 'cb', 'cb'), ('on', 'cd', 'pallet'), ('equal', 'cd', 'cd'), ('on', 'ce', 'cf'), 

16 frozenset({('attached', 'q2', 'l2'), ('equal', 'cf', 'cf'), ('equal', 'cb', 'cb'), ('equal', 'cd', 'cd'), ('in', 'cd', 'p1'), ('on', 'cc', 'cb'), ('top', 'cf', 'p2'), ('on', 'ca', 'pallet'), ('top', 'pallet', 'q2'), ('adjacent', 'l2', 'l1'), ('on', 'ce', 'cc'), ('equal', 'cc', 'cc'), ('unloaded', 'r1'), ('adjacent', 'l1', 'l2'), ('equal', 'pallet', 'pallet'), ('belong', 'k1', 'l1'), ('attached', 'p2', 'l2'), ('in', 'ca', 'p1'), ('on', 'cf', 'pallet'), ('equal', 'ce', 'ce'), ('attached', 'q1', 'l1'), ('at', 'r1', 'l2'), ('in', 'cb', 'p1'), ('empty', 'k2'), ('occupied', 'l2'), ('attached', 'p1', 'l1'), ('empty', 'k1'), ('top', 'pallet', 'q1'), ('equal', 'ca', 'ca'), ('in', 'cc', 'p1'), ('in', 'cf', 'p2'), ('top', 'cd', 'p1'), ('in', 'ce', 'p1'), ('on', 'cd', 'ce'), ('belong', 'k2', 'l2'), ('on', 'cb', 'ca')}) 9 

16 frozenset({('attached', 'q2', 'l2'), ('on', 'cf', 'cb'), ('equal', 'cf', 'cf'), ('equal', 'cb', 'cb'), ('on', 'cd', 'pallet'), ('equal', 'cd', 'cd'), ('on', 'ce', 'cf'), (

## Test planner output time

Here we will test the output time of the implemented search function. The **maximum** acceptable output time is **60 seconds** for the given domains. Please consider that a good implementation should take less than 20 seconds (depending on the machine) for any of the given problems.

In [ ]:
#Student_tests
dwr = "examples/dwr/dwr.pddl"
pb1 = "examples/dwr/pb1.pddl"
pb2 = "examples/dwr/pb2.pddl"
planner = HeuristicPlanner()

plan, time = planner.solve_file(dwr, pb1)
print("Elapsed time:", str(time) + (' Passed!' if time <= 60.0 else ' Timeout!'))

plan, time = planner.solve_file(dwr, pb2)
print("Elapsed time:", str(time) + (' Passed!' if time <= 60.0 else ' Timeout!'))


## Benchmark heuristic function (Optional)

We can now compare various planning strategies more objectively than just using runtime.

First, instrument your code with the following line immediately before the return statements of your search procedure (to collect the number of visited states):
```python
if self.stats is not None: self.stats.nodes = len(visited)
```

You will also need to implement a Breadth First Search (or a Uniform Cost Search) procedure to use as a baseline for this assignment. For that, you need to define a ```BFS_Planner``` class, derived from the ```PDDLPlanner``` class (much like the ```HeuristicPlanner``` you have above:

```python
class BFS_Planner(PDDLPlanner):
    #Positive goals and negative goals in a tuple
    def solve(self, actions, state, goals):
        pass
```

Implementing this procedure should be trivial from your implementation of $A^{*}$. 

Finally, run the code below to see how your planner compares to the simplest BFS.

In [ ]:
from pddl.bfs_planner import BFS_Planner
from pddl.heuristic_planner import HeuristicPlanner
from pddl.benchmark import PlanningBenchmark, InstanceStats

import matplotlib.pyplot as plt

benchmark = PlanningBenchmark()

for i in range(1,6):
    planner = HeuristicPlanner(heuristic=MaxHeuristic(stats=benchmark.get_instance(domain_name='examples/blocksworld/blocksworld.pddl', problem_name='examples/blocksworld/pb%d.pddl'%i )))
    planner.collect_benchmark = True
    planner.solve_file('examples/blocksworld/blocksworld.pddl','examples/blocksworld/pb%d.pddl'%i)
    

hActions, hTime = benchmark.get_stats('examples/blocksworld/blocksworld.pddl',xaxis='action',stat='time',approach='Heuristic')
hProblem, hTime = benchmark.get_stats('examples/blocksworld/blocksworld.pddl', xaxis='problem', stat='time', approach='Heuristic')
hActions, hNodes = benchmark.get_stats('examples/blocksworld/blocksworld.pddl', xaxis='action', stat='nodes',approach='Heuristic')
hActions, hCalls = benchmark.get_stats('examples/blocksworld/blocksworld.pddl', xaxis='action', stat='h_calls', approach='Heuristic')

benchmark.reset_stats()

planner = BFS_Planner()
planner.collect_benchmark = True

for i in range(1, 6):
    planner.solve_file('examples/blocksworld/blocksworld.pddl', 'examples/blocksworld/pb%d.pddl' % i)

# benchmark.plot_stat('../examples/blocksworld/blocksworld.pddl', xaxis='action', stat='time', approach='BFS')
# benchmark.plot_stat('../examples/blocksworld/blocksworld.pddl', xaxis='problem', stat='time', approach='BFS')

hActions2, hTime2 = benchmark.get_stats('examples/blocksworld/blocksworld.pddl', xaxis='action', stat='time',
                                      approach='BFS')
hProblem2, hTime2 = benchmark.get_stats('examples/blocksworld/blocksworld.pddl', xaxis='problem', stat='time',
                                      approach='BFS')
hActions2, hNodes2 = benchmark.get_stats('examples/blocksworld/blocksworld.pddl', xaxis='action', stat='nodes',
                                       approach='BFS')
hActions2, hCalls2 = benchmark.get_stats('examples/blocksworld/blocksworld.pddl', xaxis='action',
                                       stat='h_calls', approach='BFS')

fig1 = plt.figure()
ax1 = fig1.add_subplot()
ax1.plot(hActions, hTime, label = "h_max")
ax1.plot(hActions2, hTime2, label="BFS")
ax1.legend(loc='lower right')
ax1.set_title("Time Performance")
ax1.set_xlabel("Problem Actions")
ax1.set_ylabel("Time (s)")
plt.show()

fig2 = plt.figure()
ax2 = fig2.add_subplot()
ax2.plot(hActions, hNodes, label="h_max")
ax2.plot(hActions2, hNodes2, label="BFS")
ax2.legend(loc='lower right')
ax2.set_title("Expanded Nodes")
ax2.set_xlabel("Problem Actions")
ax2.set_ylabel("Expanded Nodes")
plt.show()

fig4 = plt.figure()
ax4 = fig4.add_subplot()
ax4.plot(hActions, hCalls, label="h_max")
ax4.plot(hActions2, hCalls2, label="BFS")
ax4.legend(loc='lower right')
ax4.set_title("Heuristic Function Calls")
ax4.set_xlabel("Problem Actions")
ax4.set_ylabel("H Calls")
plt.show()

fig3 = plt.figure()
ax3 = fig3.add_subplot()

x = range(len(hProblem))  # the label locations
width = 0.35  # the width of the bars

rects1 = ax3.bar([xv - width / 2 for xv in x], hTime, width, label="h_max")
rects2 = ax3.bar([xv + width / 2 for xv in x], hTime2, width, label="BFS")

# Add some text for labels, title and custom x-axis tick labels, etc.
ax3.set_xlabel('Problem Name')
ax3.set_ylabel('Time (s)')
ax3.set_title('Problem')
ax3.set_xticks(x)
ax3.set_xticklabels(hProblem)
ax3.legend()

def autolabel(rects):
    """Attach a text label above each bar in *rects*, displaying its height."""
    for rect in rects:
        height = rect.get_height()
        ax3.annotate('{:.4f}'.format(height),
                    xy=(rect.get_x() + rect.get_width() / 2, height),
                    xytext=(0, 3),  # 3 points vertical offset
                    textcoords="offset points",
                    ha='center', va='bottom')

autolabel(rects1)
autolabel(rects2)

fig3.tight_layout()
plt.show()

from IPython.display import display, Markdown, Latex

display(Markdown("# If $h_{max}$ was not faster than BFS, why was that the case?"))